In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import decoupler as dc
from scipy.stats import mannwhitneyu

%load_ext rpy2.ipython

In [2]:
%%R
suppressMessages({
    library(tidyverse)
    library(ggfortify)
    library(limma)
    library(cowplot)
    library(vsn)
    library(ggrepel)
})

In [3]:
translator_df = pd.read_csv('data/processed_data/translator_df.csv')
uniprot_to_symbol = translator_df.set_index('uniprot')['symbol'].to_dict()
symbol_to_uniprot = translator_df.set_index('symbol')['uniprot'].to_dict()

In [27]:
de_df = pd.read_csv('data/processed_data/egf_data.csv.gz')
de_df['residue'] = de_df['site_id'].str.extract(r'_([STY])\d+')
de_df['protein'] = de_df['site_id'].str.extract(r'(.+)_')
de_df['symbol'] = de_df['protein'].map(uniprot_to_symbol)
de_df['residue_site'] = de_df['site_id'].str.extract(r'_(.+)')
de_df['symbol_site'] = de_df['symbol'] + '_' + de_df['residue_site']
de_df['treatment_time'] = de_df['comparison'].str.extract(r'(\d+)min')
de_df['study_comparison'] = de_df['study'] + ' ' + de_df['treatment_time'] + 'min'
de_df['is_significant'] = np.where(de_df['adj.P.Val'] < 0.05, '*', '')

In [28]:
de_df.to_csv('supp_tables/2_egf_data.csv.gz', index=False, compression='gzip')

In [5]:
site_df = de_df.groupby(['study', 'residue'])['site_id'].nunique().reset_index()
site_df = site_df.sort_values('site_id', ascending=False)

In [ ]:
site_df.groupby('study')['site_id'].sum().sort_values(ascending=False)

In [ ]:
%%R -i site_df -w 700 -h 350
p <- site_df %>%
    mutate(site_df, study = fct_reorder(study, site_id, .fun = sum)) %>%
    mutate(residue = fct_rev(fct_reorder(residue, site_id))) %>%
    ggplot( aes(y = study, x = site_id, fill = residue, label = site_id, group = residue)) +
    geom_bar(stat = 'identity') +
    scale_fill_viridis_d() +
    theme_minimal() +
    coord_cartesian(clip = 'off') +
    labs(x = 'Number of sites') +
    ylab('Study') +
    theme_cowplot() +
    guides(x = guide_axis(angle = 45))

ggsave('figures/main/sites_per_study.pdf', p, width = 6, height = 3, dpi = 300)
p

In [8]:
def my_overlap_coefficient(input_df):
    intersection = input_df.dot(input_df.T)
    set_size = input_df.sum(axis=1)
    min_size = pd.DataFrame(np.minimum(set_size.values[:, None], set_size.values[None, :]), 
                            index=set_size.index, columns=set_size.index)
    overlap = intersection.div(min_size)
    tomask = np.triu(np.ones(overlap.shape), k = 1).astype(bool)
    overlap[tomask] = np.nan
    overlap.index.name = 'var1'
    overlap_long = overlap.reset_index().melt(id_vars='var1', var_name='var2', value_name='overlap').dropna()
    return overlap_long
def my_jaccard_index(input_df):
    intersection = input_df.dot(input_df.T)
    set_size = input_df.sum(axis=1)
    union = pd.DataFrame(set_size.values[:, None] + set_size.values[None, :] - intersection.values, 
                         index=set_size.index, columns=set_size.index)
    jaccard = intersection.div(union)
    tomask = np.triu(np.ones(jaccard.shape), k = 1).astype(bool)
    jaccard[tomask] = np.nan
    jaccard.index.name = 'var1'
    jaccard_long = jaccard.reset_index().melt(id_vars='var1', var_name='var2', value_name='overlap').dropna()
    return jaccard_long

In [9]:
id_de = de_df[['study', 'site_id']].drop_duplicates()
id_de['is'] = 1
wide_id = id_de.pivot(index='study', columns='site_id', values='is').fillna(0)
id_overlap_coef = my_jaccard_index(wide_id)
id_overlap_coef.to_csv('/tmp/toplot.csv')

In [ ]:
id_overlap_coef[id_overlap_coef['overlap'] != 1]['overlap'].mean()

In [ ]:
%%R -w 700 -h 350
toplot <- read_csv('/tmp/toplot.csv') 

p <- toplot %>%
  mutate(var1 = factor(var1, levels = rev(unique(var1))),
         var2 = factor(var2, levels = unique(var2))) %>%
  ggplot(aes(x = var1, y = var2, fill = overlap)) +
  geom_tile() +
  scale_fill_viridis_c(option = 'viridis', name = 'Jaccard') +
  geom_label(aes(label = round(overlap, 2)), fill = 'white') +
  theme_cowplot() +
  theme(
        axis.text.x = element_text(angle = 45, hjust = 1),
        axis.ticks.x = element_blank(),axis.title.x = element_blank(), 
        axis.title.y = element_blank()) 
ggsave('figures/main/study_id_overlap.pdf', p, width = 6, height = 4.5, dpi = 300, bg = 'transparent')
p

In [ ]:
de_df_agg = de_df.groupby(['site_id', 'study']).agg({'logFC': 'mean'}).reset_index()
wide_de = de_df_agg.pivot(index='site_id', columns='study', values='logFC')
wide_de = wide_de.dropna()
wide_de.shape

In [14]:
corr_df = wide_de.corr( method='pearson')
tomask = np.triu(np.ones(corr_df.shape), k = 1).astype(bool)
corr_df[tomask] = np.nan
corr_df.index.name = 'var1'
corr_long = corr_df.reset_index().melt(id_vars='var1', var_name='var2', value_name='overlap').dropna()
corr_long.to_csv('/tmp/corr.csv')

In [ ]:
corr_long[corr_long['overlap'] != 1]['overlap'].mean()

In [ ]:
%%R -w 600 -h 400
p <- read_csv('/tmp/corr.csv') %>%
  mutate(var1 = factor(var1, levels = rev(unique(var1))),
         var2 = factor(var2, levels = unique(var2))) %>%
  ggplot(aes(x = var1, y = var2, fill = overlap)) +
  geom_tile() +
  scale_fill_viridis_c(option = 'viridis', name = 'Pearson') +
  geom_label(aes(label = round(overlap, 2)), fill = 'white') +
  theme_cowplot() +
  theme(
    axis.title.x = element_blank(), 
        axis.title.y = element_blank(),
        axis.text.x = element_text(angle = 45, hjust = 1) )
ggsave('figures/supp/study_corr.png', p, width = 7, height = 5, dpi = 300, bg = 'transparent')
p

In [17]:
egf_pathway = pd.read_csv('data/processed_data/signor_egf.tsv', sep='\t')
int_sites = egf_pathway['IDB'] + '_' + egf_pathway['RESIDUE']
int_sites = int_sites.str.replace('Thr', 'T').str.replace('Tyr', 'Y').str.replace('Ser', 'S')
int_sites = int_sites.dropna()
annotated_de = de_df.copy()

In [20]:
resdf = []
for int_study in annotated_de['study_comparison'].unique():
    study_df = annotated_de[annotated_de['study_comparison'] == int_study]
    egf_sites = study_df[study_df['site_id'].isin(int_sites)]
    non_egf_sites = study_df[~study_df['site_id'].isin(int_sites)]
    res = mannwhitneyu(egf_sites['logFC'].abs(), non_egf_sites['logFC'].abs())
    diff = egf_sites['logFC'].abs().mean() - non_egf_sites['logFC'].abs().mean()
    resdf.append([int_study, res.pvalue, diff])
resdf = pd.DataFrame(resdf, columns=['study_comparison', 'pvalue', 'diff'])
from statsmodels.stats.multitest import multipletests
resdf['adj_pvalue'] = multipletests(resdf['pvalue'], method='fdr_bh')[1]

resdf.to_csv('/tmp/egf_sites_diff.csv')

In [ ]:
%%R -w 600 -h 400

resdf <- read_csv('/tmp/egf_sites_diff.csv')

p <- resdf %>%
    mutate(study_comparison = fct_reorder(study_comparison, diff)) %>%
    ggplot(aes(y = study_comparison, x = diff)) +
    geom_bar(stat = 'identity', color = 'black', fill = 'lightgray') +
    theme_cowplot() +
    theme(axis.text.x = element_text(angle = 45, hjust = 1)) +
    labs(x = 'Absolute logFC\ndifference\n(EGF sites)') +
    scale_color_manual(values = c('TRUE' = 'red', 'FALSE' = 'black')) +
    theme(axis.title.y = element_blank()) 
ggsave('figures/main/egf_sites_diff.pdf', p, width = 5.5, height = 6, dpi = 300, bg = 'transparent')
p

In [ ]:
egf_de_df = de_df[de_df['site_id'].isin(int_sites)].copy()
egf_toplot = egf_de_df.groupby(['study', 'site_id']).apply(lambda x: x.loc[x['logFC'].abs().idxmax()]).reset_index(drop=True)
egf_toplot.to_csv('/tmp/toplot.csv')
egf_de_df[['study', 'site_id']].drop_duplicates().groupby('study').size()

In [ ]:
%%R -w 700 -h 250

toplot <- read_csv('/tmp/toplot.csv') %>%
  arrange(study, treatment_time) %>%
  mutate(study_comparison = fct_rev(fct_inorder(study_comparison))) %>%
  mutate(symbol_site = fct_reorder(symbol_site, logFC)) %>%
  mutate(is_this_study = if_else(grepl('This study', study), 'This Study', 'Others'))

p <- toplot %>%
  ggplot(aes(y = study, x = symbol_site, fill = logFC)) + 
  geom_point(color = 'black', pch = 21, size = 7) +
  geom_text(aes(label = is_significant), size = 3) +
  scale_fill_gradient2( low = "blue", mid = "white", high = "red", midpoint = 0, limits = c(-2, 2), breaks = c(-2, -1, 0, 1, 2),
                        oob = scales::squish) +
  guides(x = guide_axis(angle = 45)) +
  theme_cowplot() +
  theme(  axis.title.x = element_blank(), axis.title.y = element_blank())

ggsave('figures/main/egf_sites_dotplot.pdf', p, width = 12, height = 3.5, dpi = 300, bg = 'transparent')
p

In [ ]:
egfr_sites = de_df[de_df['symbol'] == 'EGFR']['site_id'].unique()
egfr_de_df = de_df[de_df['site_id'].isin( egfr_sites  )].copy()
egfr_de_df['is_significant'] = np.where(egfr_de_df['adj.P.Val'] < 0.05, '*', '')
egfr_toplot = egfr_de_df.groupby(['study', 'site_id']).apply(lambda x: x.loc[x['logFC'].abs().idxmax()]).reset_index(drop=True)
egfr_de_df.to_csv('/tmp/toplot.csv')

In [ ]:
%%R -w 750 -h 250
toplot <- read_csv('/tmp/toplot.csv') %>%
  mutate(position =  as.numeric(str_replace(site_id, '.*_.', ''))) %>%
  mutate(residue_site = fct_reorder(residue_site, position))

p <- toplot %>%
  ggplot(aes(y = study, x = residue_site, fill = logFC, label = is_significant)) + 
  geom_point(color = 'black', pch = 21, size = 7) +
  geom_text(size = 3) +
  scale_fill_gradient2( low = "blue", mid = "white", high = "red", midpoint = 0, limits = c(-2, 2), breaks = c(-2, -1, 0, 1, 2),
                        oob = scales::squish) +
  
  guides(x = guide_axis(angle = 45)) +
  theme_cowplot() +
  theme( axis.title.y = element_blank()) +
  xlab('EGFR')
ggsave('figures/main/egfr_sites_dotplot.pdf', p,  width = 12, height = 3.5, dpi = 300, bg = 'transparent')
p